In [72]:
import numpy as np
import pandas as pd
import pyarrow as pa
import pyarrow.parquet as pq
import os
import argparse
import random
import torchaudio
import pyloudnorm as pyln

rate = 16000
meter = pyln.Meter(rate)

table = pq.read_table(os.path.join('..', 'data', 'TIMIT', 'train-00000-of-00002.parquet')).to_pandas()


In [79]:
level = -20.0

In [95]:
table.shape

(2520, 2)

In [101]:
def extract(n):
    data = table['audio'][n]['array']
    # Normalize each sample before concat
    loudness = meter.integrated_loudness(data)
    return pyln.normalize.loudness(data, loudness, level)

def extracts(duration, seed=1234, gap=0.5):
    silence = np.zeros((round(gap * rate), ))
    random.seed(seed)
    index = list(range(table.shape[0]))
    random.shuffle(index)
    res = np.zeros((0,))
    while res.shape[0] < duration * rate:
        res = np.concatenate([res, extract(index.pop()), silence])
    return res

In [118]:
from IPython.display import Audio

waveform = extracts(100.0)
Audio(waveform, rate=rate)

/home/nwhitehead/projects/lipsync/venv/lib/python3.12/site-packages/pyloudnorm/normalize.py:62: UserWarning: Possible clipped samples in output.
  warnings.warn("Possible clipped samples in output.")
/home/nwhitehead/projects/lipsync/venv/lib/python3.12/site-packages/pyloudnorm/normalize.py:62: UserWarning: Possible clipped samples in output.
  warnings.warn("Possible clipped samples in output.")
/home/nwhitehead/projects/lipsync/venv/lib/python3.12/site-packages/pyloudnorm/normalize.py:62: UserWarning: Possible clipped samples in output.
  warnings.warn("Possible clipped samples in output.")
/home/nwhitehead/projects/lipsync/venv/lib/python3.12/site-packages/pyloudnorm/normalize.py:62: UserWarning: Possible clipped samples in output.
  warnings.warn("Possible clipped samples in output.")
/home/nwhitehead/projects/lipsync/venv/lib/python3.12/site-packages/pyloudnorm/normalize.py:62: UserWarning: Possible clipped samples in output.
  warnings.warn("Possible clipped samples in output.")


In [125]:
waveform.shape
import torch
torch.Tensor(waveform.reshape([1, -1])).shape

torch.Size([1, 1654741])

In [147]:
torchaudio.save('test.mp3', torch.Tensor(waveform.reshape([1, -1])), sample_rate=rate, backend='ffmpeg')

In [86]:
x = list(range(10))
x

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9]

In [88]:
random.shuffle(x)
x

[6, 9, 0, 8, 4, 1, 3, 2, 7, 5]

In [52]:
data = extract(100)
loudness = meter.integrated_loudness(data)

In [53]:
loudness

np.float64(-43.69258096947796)

In [55]:
loudness_normalized_audio = pyln.normalize.loudness(data, loudness, -18.0)

In [56]:
Audio(loudness_normalized_audio, rate=rate)